### Flatten Bronze Data

In [0]:
from pyspark.sql.functions import when,col,lit
from delta.tables import DeltaTable
#Read Parquet file
# raw_df = spark.read.parquet('dbfs:/FileStore/tables/movie_bronze.parquet')
raw_df = spark.read.load('dbfs:/FileStore/tables/movie_bronze.delta')

#flatten movie data
df = (raw_df.select(col('movie').alias('nested_json'),
                   'movie.BackdropUrl',
                   'movie.Budget',
                   'movie.CreatedDate',
                   'movie.Id',
                   'movie.ImdbUrl',
                   'movie.Overview',
                   'movie.PosterUrl',
                   'movie.Price',
                   'movie.ReleaseDate',
                   'movie.Revenue',
                   'movie.RunTime',
                   'movie.Tagline',
                   'movie.TmdbUrl',
                   'movie.Genres',
                   'movie.OriginalLanguage',
                   'DataSource',
                   'IngestTime',
                   'ModifiedDate',
                   'Status'))


### Quarantine the Bad Data

In [0]:
display(df.filter((col('RunTime')<0)).count())

#No such records

0

### Creating Lookup Table(Genres and OriginalLanguage) and movie_silver

In [0]:
genres_silver = df.select('Id','Genres')
originallanguage_silver = df.select('Id','Originallanguage')
movie_silver = df.select([c for c in df.columns if c not in ['Id','Originallanguage']])

### Question:Certain movies have valid ID for the genre, but the name of the genre is missing

#### Do we need to fix this? If we do, where should we fix this?
Answer: No. If we need to fix this then we should utilize a dimension table to find the value based on id.

#### If not, why don’t we need to fix this?
Answer: We already have id for those genre and we can use dimension table to find it if required.

### Question:Let’s assume all the movies should have a minimum budget of 1 million

#### Where should we fix this? (Raw/Bronze/Silver)
Answer: Silver Table. 
#### If a movie has a budget of less than 1 million, we should replace it with 1 million
See code below

In [0]:
movie_silver.withColumn('Budget', when(movie_silver['Budget']<1000000, 1000000))

Out[21]: DataFrame[nested_json: struct<BackdropUrl:string,Budget:double,CreatedDate:string,Id:bigint,ImdbUrl:string,OriginalLanguage:string,Overview:string,PosterUrl:string,Price:double,ReleaseDate:string,Revenue:double,RunTime:bigint,Tagline:string,Title:string,TmdbUrl:string,genres:array<struct<id:bigint,name:string>>>, BackdropUrl: string, Budget: int, CreatedDate: string, ImdbUrl: string, Overview: string, PosterUrl: string, Price: double, ReleaseDate: string, Revenue: double, RunTime: bigint, Tagline: string, TmdbUrl: string, Genres: array<struct<id:bigint,name:string>>, OriginalLanguage: string, DataSource: string, IngestTime: timestamp, ModifiedDate: timestamp, Status: string]

### Question: We have some movies that are showing up in more than one movie file.

####       How do we ensure only one record shows up in our silver table?
Using dropDuplicate()

#### Storing silver table and update bronze table

In [0]:
display(movie_silver)

nested_json BackdropUrl Budget CreatedDate ImdbUrl Overview PosterUrl Price ReleaseDate Revenue RunTime Tagline TmdbUrl Genres OriginalLanguage DataSource IngestTime ModifiedDate Status List(https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg, 1.6E8, 2021-04-03T16:51:30.1633333, 1, https://www.imdb.com/title/tt1375666, en, Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious., https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg, 9.9, 2010-07-15T00:00:00, 8.25532764E8, 148, Your mind is the scene of the crime., Inception, https://www.themoviedb.org/movie/27205, List(List(1, Adventure), List(6, Action), List(13, Science Fiction))) https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg 1.6E8 2021-04-03T16:51:30.1633333 https://www.imdb.com/title/tt1375666 Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious. https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg 9.9 2010-07-15T00:00:00 8.25532764E8 148 Your mind is the scene of the crime. https://www.themoviedb.org/movie/27205 List(List(1, Adventure), List(6, Action), List(13, Science Fiction)) en movie_dataset 2023-08-07T02:15:20.827+0000 2023-08-07T02:15:20.860+0000 new List(https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg, 1.65E8, 2021-04-03T16:51:30.1633333, 2, https://www.imdb.com/title/tt0816692, en, The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage., https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg, 9.9, 2014-11-05T00:00:00, 6.75120017E8, 169, Mankind was born on Earth. It was never meant to die here., Interstellar, https://www.themoviedb.org/movie/157336, List(List(1, Adventure), List(4, Drama), List(13, Science Fiction))) https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg 1.65E8 2021-04-03T16:51:30.1633333 https://www.imdb.com/title/tt0816692 The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage. https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg 9.9 2014-11-05T00:00:00 6.75120017E8 169 Mankind was born on Earth. It was never meant to die here. https://www.themoviedb.org/movie/157336 List(List(1, Adventure), List(4, Drama), List(13, Science Fiction)) en movie_dataset 2023-08-07T02:15:20.827+0000 2023-08-07T02:15:20.860+0000 new List(https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg, 1.85E8, 2021-04-03T16:51:30.1633333, 3, https://www.imdb.com/title/tt0468569, en, Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker., https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg, 9.9, 2008-07-16T00:00:00, 1.004558444E9, 152, Why So Serious?, The Dark Knight, https://www.themoviedb.org/movie/155, List(List(4, Drama), List(6, Action), List(10, Thriller), List(11, Crime))) https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg 1.85E8 2021-04-03T16:51:30.1633333 https://www.imdb.com/title/tt0468569 Batman raises the stakes in his war on crime. With the 

In [0]:
from delta.tables import DeltaTable

bronzePath = 'dbfs:/FileStore/tables/movie_bronze.delta'

bronzeTable = DeltaTable.forPath(spark, bronzePath)
silverAugmented = movie_silver.withColumn("status", lit("loaded"))

update_match = "bronze.movie = clean.nested_json"
update = {"status": "clean.status"}

(
    bronzeTable.alias("bronze")
    .merge(silverAugmented.alias("clean"), update_match)
    .whenMatchedUpdate(set=update)
    .execute()
)

In [0]:
display(spark.read.load('dbfs:/FileStore/tables/movie_bronze.delta').select('Status'))

Status loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loaded loa